In [0]:
from pyspark.sql.functions import col, split, concat, lit, substring, upper, udf, trim
from pyspark.sql.types import DoubleType, IntegerType, StringType

In [0]:
trucksDF = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/nagpritamnaik@gmail.com/trucks.csv")
trucksMGDF = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/nagpritamnaik@gmail.com/trucks_mg.csv")
geolocDF = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/nagpritamnaik@gmail.com/geolocation.csv")

# display(trucksDF)
# display(trucksMGDF)
# display(geolocDF)

In [0]:
# create a temp view for the datset for running sql queries 
trucksDF.createOrReplaceTempView("trucks")

In [0]:
# Unpivot the dataset for the trucks dataset
l = []
seperator = ', '
A = ['jun13_miles','jun13_gas','may13_miles','may13_gas','apr13_miles','apr13_gas','mar13_miles','mar13_gas','feb13_miles','feb13_gas','jan13_miles','jan13_gas','dec12_miles','dec12_gas','nov12_miles','nov12_gas','oct12_miles','oct12_gas','sep12_miles','sep12_gas','aug12_miles','aug12_gas','jul12_miles','jul12_gas','jun12_miles','jun12_gas','may12_miles','may12_gas','apr12_miles','apr12_gas','mar12_miles','mar12_gas','feb12_miles','feb12_gas','jan12_miles','jan12_gas',
'dec11_miles','dec11_gas','nov11_miles','nov11_gas','oct11_miles','oct11_gas','sep11_miles','sep11_gas','aug11_miles','aug11_gas','jul11_miles','jul11_gas','jun11_miles','jun11_gas','may11_miles','may11_gas','apr11_miles','apr11_gas','mar11_miles','mar11_gas','feb11_miles','feb11_gas','jan11_miles','jan11_gas',
'dec10_miles','dec10_gas','nov10_miles','nov10_gas','oct10_miles','oct10_gas','sep10_miles','sep10_gas','aug10_miles','aug10_gas','jul10_miles','jul10_gas','jun10_miles','jun10_gas','may10_miles','may10_gas','apr10_miles','apr10_gas','mar10_miles','mar10_gas','feb10_miles','feb10_gas','jan10_miles','jan10_gas',
'dec09_miles','dec09_gas','nov09_miles','nov09_gas','oct09_miles','oct09_gas','sep09_miles','sep09_gas','aug09_miles','aug09_gas','jul09_miles','jul09_gas','jun09_miles','jun09_gas','may09_miles','may09_gas','apr09_miles','apr09_gas','mar09_miles','mar09_gas','feb09_miles','feb09_gas','jan09_miles','jan09_gas']
B = seperator.join(A).split(",")
n = len(A)
for a in range(len(A)):
    l.append("'{}'".format(A[a]) + ", " + B[a])

k = seperator.join(l)
# print(n)
# print(k)

unpivotDF = spark.sql("""SELECT driverid,truckid,model, stack({0}, {1}) as (Month_Year, Miles_Gas_Values) from trucks""".format(n, k))
# display(unpivotDF)

In [0]:
#filter the dataset for miles value
unpivotDFmiles = unpivotDF.filter(col("Month_Year").like("%miles%")) \
    .withColumn("month",trim(upper(substring(split(col("Month_Year"),'_')[0],0,3)))) \
    .withColumn("year",concat(lit("20"),substring(split(col("Month_Year"),'_')[0],4,2)).cast(IntegerType())) \
    .withColumnRenamed("Miles_Gas_Values","Miles") \
    .withColumn("Miles",col("Miles").cast(DoubleType())) \
    .drop("Month_Year") \
    .selectExpr("trim(driverid) as driverid", "trim(truckid) as truckid", "trim(model) as model", "trim(month) as month", "year", "Miles")
    
# display(unpivotDFmiles)

In [0]:
#filter the dataset for gas value
unpivotDFgas = unpivotDF.filter(col("Month_Year").like("%gas%")) \
    .withColumn("month",trim(upper(substring(split(col("Month_Year"),'_')[0],0,3)))) \
    .withColumn("year",concat(lit("20"),substring(split(col("Month_Year"),'_')[0],4,2)).cast(IntegerType())) \
    .withColumnRenamed("Miles_Gas_Values","Gas") \
    .withColumn("Gas",col("Gas").cast(DoubleType())) \
    .drop("Month_Year") \
    .selectExpr("trim(driverid) as driverid", "trim(truckid) as truckid", "trim(model) as model", "trim(month) as month", "year", "Gas")
    
# display(unpivotDFgas)

In [0]:
# Perform the join between unpivotDFmiles and unpivotDFgas to extract Miles and Gas as separate columns in the dataset for each Month and year, joined on driverid, truckid, model, month and year

transformDF = unpivotDFmiles.join(unpivotDFgas, (unpivotDFmiles.driverid == unpivotDFgas.driverid) & (unpivotDFmiles.truckid == unpivotDFgas.truckid) & (unpivotDFmiles.model == unpivotDFgas.model) & (unpivotDFmiles.month == unpivotDFgas.month) & (unpivotDFmiles.year == unpivotDFgas.year))

# select relevant columns from both Dataframes
seltransformDF = transformDF.select(unpivotDFmiles.driverid, unpivotDFmiles.truckid, unpivotDFmiles.model, unpivotDFmiles.month, unpivotDFmiles.year, unpivotDFmiles.Miles, unpivotDFgas.Gas)

# display(seltransformDF)

In [0]:
#split the Date column into Month and Year Column for the Dataframe 
preprocess_trucksMGDF = trucksMGDF.withColumn("Month",split(col("Date"),'/')[1].cast(IntegerType()))\
    .withColumn("year",split(col("Date"),'/')[2].cast(IntegerType()))

# display(preprocess_trucksMGDF)

In [0]:
#udf function to categorize numeric month value to Mon to match the above dataset

def udf_month(mon):
    dict_month = {1:"JAN", 2:"FEB", 3:"MAR", 4:"APR", 5:"MAY", 6:"JUN", 7:"JUL", 8:"AUG", 9:"SEP", 10:"OCT", 11:"NOV", 12:"DEC"}
    if(mon in list(dict_month.keys())):
        return dict_month[mon]
    return None
spark_udf_month = udf(lambda mon: udf_month(mon), StringType())

In [0]:
#add month column to the pre_process dataset
seltransform_trucksMGDF = preprocess_trucksMGDF.withColumn("month", spark_udf_month("Month")) \
    .drop(col("Date")) \
    .selectExpr("driverid", "truckid", "model", "month", "year", "cast(Miles as double) as Miles", "cast(Gas as double) as Gas") \
    .sort(col("year").desc())
# display(seltransform_trucksMGDF)

In [0]:
#perform a union between the trucks(unpivoted) and truck_mg dataset, 
#Final Dataset

union_truckDF = seltransformDF.union(seltransform_trucksMGDF).sort(col("year").desc())
display(union_truckDF)

driverid truckid model month year Miles Gas A5 A5 Hino MAY 2016 10233.0 1825.0 A17 A17 Western Star MAY 2016 12939.0 2823.0 A29 A29 Ford MAY 2016 12091.0 2606.0 A41 A41 Navistar MAY 2016 8490.0 1636.0 A53 A53 Navistar MAY 2016 9796.0 2049.0 A65 A65 Hino MAY 2016 14214.0 2997.0 A77 A77 Ford MAY 2016 13187.0 2752.0 A89 A89 Caterpillar MAY 2016 14955.0 3344.0 A1 A1 Freightliner JAN 2015 9217.0 1914.0 A2 A2 Ford FEB 2015 12058.0 2335.0 A3 A3 Ford MAR 2015 13652.0 2899.0 A4 A4 Kenworth APR 2015 12687.0 2439.0 A6 A6 Caterpillar JUN 2015 14488.0 2883.0 A7 A7 Ford JUL 2015 10938.0 2231.0 A8 A8 Navistar AUG 2015 11392.0 2280.0 A9 A9 Volvo SEP 2015 12601.0 2515.0 A10 A10 Peterbilt OCT 2015 13699.0 2583.0 A11 A11 Peterbilt NOV 2015 12447.0 2596.0 A12 A12 Caterpillar DEC 2015 10006.0 2055.0 A13 A13 Oshkosh JAN 2015 9740.0 1792.0 A14 A14 Crane FEB 2015 10608.0 1822.0 A15 A15 Ford MAR 2015 9650.0 2025.0 A16 A16 Navistar APR 2015 10953.0 2066.0 A18 A18 Caterpillar JUN 2015 11102.0 2319.0 A19 A19 Caterpillar JUL 2015 14295.0 3446.0 A20 A20 Western Star AUG 2015 11706.0 2773.0 A21 A21 Hino SEP 2015 13179.0 3273.0 A22 A22 Caterpillar OCT 2015 11038.0 2438.0 A23 A23 Ford NOV 2015 13736.0 3136.0 A24 A24 Navistar DEC 2015 12038.0 2490.0 A25 A25 Volvo JAN 2015 11408.0 2654.0 A26 A26 Peterbilt FEB 2015 11612.0 2348.0 A27 A27 Peterbilt MAR 2015 11147.0 2464.0 A28 A28 Caterpillar APR 2015 10216.0 2246.0 A30 A30 Ford JUN 2015 14366.0 2923.0 A31 A31 Kenworth JUL 2015 10690.0 1980.0 A32 A32 Hino AUG 2015 10517.0 2098.0 A33 A33 Caterpillar SEP 2015 13125.0 2650.0 A34 A34 Freightliner OCT 2015 12168.0 2569.0 A35 A35 Ford NOV 2015 11740.0 2229.0 A36 A36 Ford DEC 2015 15008.0 2615.0 A37 A37 Kenworth JAN 2015 14819.0 3316.0 A38 A38 Hino FEB 2015 13834.0 2414.0 A39 A39 Caterpillar MAR 2015 13752.0 2896.0 A40 A40 Ford APR 2015 10876.0 2630.0 A42 A42 Volvo JUN 2015 9734.0 1989.0 A43 A43 Peterbilt JUL 2015 11657.0 2472.0 A44 A44 Peterbilt AUG 2015 13505.0 2959.0 A45 A45 Caterpillar SEP 2015 10591.0 2035.0 A46 A46 Volvo OCT 2015 14498.0 3104.0 A47 A47 Peterbilt NOV 2015 13115.0 2672.0 A48 A48 Peterbilt DEC 2015 12603.0 2287.0 A49 A49 Caterpillar JAN 2015 12444.0 2355.0 A50 A50 Oshkosh FEB 2015 14917.0 3153.0 A51 A51 Crane MAR 2015 9423.0 2214.0 A52 A52 Ford APR 2015 12971.0 2545.0 A54 A54 Western Star JUN 2015 14969.0 2760.0 A55 A55 Caterpillar JUL 2015 11401.0 2217.0 A56 A56 Caterpillar AUG 2015 14241.0 2790.0 A57 A57 Freightliner SEP 2015 9507.0 2193.0 A58 A58 Ford OCT 2015 10074.0 1826.0 A59 A59 Ford NOV 2015 13739.0 2744.0 A60 A60 Caterpillar DEC 2015 9834.0 1886.0 A61 A61 Freightliner JAN 2015 14092.0 3058.0 A62 A62 Ford FEB 2015 11441.0 2061.0 A63 A63 Ford MAR 2015 13364.0 2747.0 A64 A64 Kenworth APR 2015 11865.0 2230.0 A66 A66 Caterpillar JUN 2015 12719.0 2718.0 A67 A67 Ford JUL 2015 12458.0 2460.0 A68 A68 Navistar AUG 2015 11411.0 2164.0 A69 A69 Volvo SEP 2015 12165.0 2231.0 A70 A70 Peterbilt OCT 2015 13148.0 2665.0 A71 A71 Peterbilt NOV 2015 11371.0 2239.0 A72 A72 Caterpillar DEC 2015 9962.0 2118.0 A73 A73 Oshkosh JAN 2015 14103.0 3337.0 A74 A74 Kenworth FEB 2015 10959.0 1971.0 A75 A75 Hino MAR 2015 11603.0 2267.0 A76 A76 Caterpillar APR 2015 13733.0 2865.0 A78 A78 Navistar JUN 2015 8693.0 1593.0 A79 A79 Volvo JUL 2015 15548.0 3355.0 A80 A80 Peterbilt AUG 2015 11108.0 2618.0 A81 A81 Peterbilt SEP 2015 9506.0 2038.0 A82 A82 Caterpillar OCT 2015 9951.0 2004.0 A83 A83 Oshkosh NOV 2015 12388.0 2519.0 A84 A84 Freightliner DEC 2015 11417.0 2070.0 A85 A85 Ford JAN 2015 15319.0 2707.0 A86 A86 Ford FEB 2015 9324.0 1636.0 A87 A87 Kenworth MAR 2015 10958.0 2417.0 A88 A88 Hino APR 2015 9653.0 1994.0 A90 A90 Ford JUN 2015 9163.0 1992.0 A91 A91 Navistar JUL 2015 10348.0 1970.0 A92 A92 Volvo AUG 2015 13617.0 2960.0 A93 A93 Navistar SEP 2015 9433.0 1902.0 A94 A94 Volvo OCT 2015 13296.0 2474.0 A95 A95 Peterbilt NOV 2015 14670.0 3328.0 A96 A96 Peterbilt DEC 2015 12738.0 2637.0 A97 A97 Caterpillar JAN 2015 13489.0 2425.0 A98 A98 Volvo FEB 2015 10732.0 2238.0 A99 A99 Peterbi

In [0]:
#extract driverId, truckId and Model names from the union of dataset 

Idlist_Df = union_truckDF.select("driverid","truckid","model").distinct()

#join between geolocation dataset and Idlist_Df for analysis dataset 
join_geolocDF = Idlist_Df.join(geolocDF, (trim(Idlist_Df.driverid) == trim(geolocDF.driverid)) & (trim(Idlist_Df.truckid) == trim(geolocDF.truckid))) \
    .drop(geolocDF["driverid"], geolocDF["truckid"])
display(join_geolocDF)


driverid truckid model event latitude longitude city state velocity event_ind idling_ind A54 A54 Western Star normal 38.440467 -122.714431 Santa Rosa California 17 0 0 A20 A20 Western Star normal 36.977173 -121.899402 Aptos California 27 0 0 A40 A40 Ford overspeed 37.957702 -121.29078 Stockton California 77 1 0 A31 A31 Kenworth normal 39.409608 -123.355566 Willits California 22 0 0 A71 A71 Peterbilt normal 33.683947 -117.794694 Irvine California 43 0 0 A50 A50 Oshkosh normal 38.40765 -122.947713 Occidental California 0 0 1 A51 A51 Crane normal 37.639097 -120.996878 Modesto California 0 0 1 A19 A19 Caterpillar normal 37.962146 -122.345526 San Pablo California 0 0 1 A77 A77 Ford normal 37.962146 -122.345526 San Pablo California 25 0 0 A92 A92 Volvo normal 37.484938 -119.966284 Mariposa California 0 0 1 A89 A89 Caterpillar normal 39.017396 -122.057748 Arbuckle California 38 0 0 A86 A86 Ford normal 32.715329 -117.157255 San Diego California 45 0 0 A5 A5 Hino unsafe following distance 41.526509 -124.038407 Klamath California 33 1 0 A54 A54 Western Star normal 35.373292 -119.018712 Bakersfield California 19 0 0 A48 A48 Peterbilt overspeed 38.752124 -121.288006 Roseville California 77 1 0 A2 A2 Ford normal 32.61768 -116.187424 Jacumba California 50 0 0 A98 A98 Volvo normal 33.19587 -117.379483 Oceanside California 27 0 0 A10 A10 Peterbilt normal 40.761243 -123.994778 Kneeland California 0 0 1 A12 A12 Caterpillar normal 37.968812 -121.668008 Knightsen California 59 0 0 A43 A43 Peterbilt normal 37.968812 -121.668008 Knightsen California 45 0 0 A65 A65 Hino normal 37.484938 -119.966284 Mariposa California 0 0 1 A62 A62 Ford normal 34.106676 -117.806726 San Dimas California 39 0 0 A94 A94 Volvo unsafe following distance 37.941325 -122.484704 San Quentin California 0 1 1 A68 A68 Navistar normal 38.440467 -122.714431 Santa Rosa California 51 0 0 A49 A49 Caterpillar lane departure 39.150171 -123.207783 Ukiah California 41 1 0 A72 A72 Caterpillar normal 37.957702 -121.29078 Stockton California 0 0 1 A10 A10 Peterbilt normal 34.106676 -117.806726 San Dimas California 46 0 0 A68 A68 Navistar normal 34.500831 -117.185876 Apple Valley California 16 0 0 A51 A51 Crane normal 33.846404 -118.046731 La Palma California 15 0 0 A7 A7 Ford normal 40.563763 -122.238892 Palo Cedro California 40 0 0 A11 A11 Peterbilt normal 39.409608 -123.355566 Willits California 31 0 0 A8 A8 Navistar normal 38.440467 -122.714431 Santa Rosa California 25 0 0 A37 A37 Kenworth normal 34.435829 -119.827639 Goleta California 16 0 0 A9 A9 Volvo normal 38.716687 -121.364422 Antelope California 67 0 0 A34 A34 Freightliner normal 38.440467 -122.714431 Santa Rosa California 68 0 0 A38 A38 Hino normal 33.663357 -116.310009 La Quinta California 72 0 0 A56 A56 Caterpillar normal 34.435829 -119.827639 Goleta California 0 0 1 A27 A27 Peterbilt normal 38.40765 -122.947713 Occidental California 18 0 0 A26 A26 Peterbilt normal 34.44805 -119.242889 Ojai California 19 0 0 A58 A58 Ford normal 38.716687 -121.364422 Antelope California 39 0 0 A57 A57 Freightliner normal 36.471865 -6.196595 San Fernando California 16 0 0 A68 A68 Navistar normal 33.743076 -117.109197 Homeland California 28 0 0 A17 A17 Western Star normal 37.957702 -121.29078 Stockton California 16 0 0 A93 A93 Navistar normal 38.440467 -122.714431 Santa Rosa California 37 0 0 A37 A37 Kenworth normal 37.441883 -122.143019 Palo Alto California 18 0 0 A33 A33 Caterpillar normal 37.941325 -122.484704 San Quentin California 63 0 0 A33 A33 Caterpillar normal 40.761243 -123.994778 Kneeland California 34 0 0 A69 A69 Volvo normal 35.373292 -119.018712 Bakersfield California 45 0 0 A22 A22 Caterpillar normal 39.150171 -123.207783 Ukiah California 30 0 0 A98 A98 Volvo normal 37.941325 -122.484704 San Quentin California 42 0 0 A100 A100 Peterbilt normal 34.136119 -117.865339 Glendora California 0 0 1 A15 A15 Ford normal 39.230151 -121.136075 Rough and Ready California 42 0 0 A66 A66 Caterpillar normal 36.852455 -121.401602 Hollister Californ